In [13]:
from IPython.display import display
import numpy as np
# import modin.pandas as pd
import pandas as pd
import datetime
import time
import gc
import matplotlib.pyplot as plt
import seaborn as sns
import lightgbm as lgb


from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import AdaBoostRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.linear_model import (
    LinearRegression, Ridge, Lasso, RandomizedLasso)
from sklearn.model_selection import StratifiedKFold
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import mean_squared_error
from sklearn.metrics import accuracy_score
from sklearn.model_selection import KFold
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.feature_selection import RFECV
from sklearn.feature_selection import RFE, f_regression

import itertools

import warnings
import json

warnings.filterwarnings('ignore')

plt.style.use("fivethirtyeight")
sns.set_style({'font.sans-serif': ['simsun', 'Arial']})
sns.set_style('darkgrid', {'font.sans-serif': ['simhei', 'Arial']})
%matplotlib inline

# np.random.seed(4590)
nf_data_path = r'../../../Data/noFinacialFeatures.csv'
f_data_path = r'../../../Data//FinacialFeatures.csv'

# flevel = json.load(open(r'./feature_level.json'))

In [14]:
nf_df = pd.read_csv(nf_data_path)
f_df = pd.read_csv(f_data_path)

In [15]:
df = pd.DataFrame()
df = nf_df.copy()
f_df.drop(['企业总评分'], axis=1, inplace=True)
df = df.merge(f_df, how='left', on='企业编号')

In [16]:
y = df[['企业编号', '企业总评分']]
x = df.drop(['企业总评分'], axis=1)

In [17]:
xtrain, xtest, ytrain, ytest = train_test_split(
    x, y, test_size=0.2, random_state=31)
ytrain_id = ytrain['企业编号']
ytrain = ytrain['企业总评分']
ytest_id = ytest['企业编号']
ytest = ytest['企业总评分']
print(xtrain.shape, xtest.shape, ytrain.shape, ytest.shape)

id_train = xtrain['企业编号']
id_test = xtest['企业编号']
xtrain.drop(['企业编号'], axis=1, inplace=True)
xtest.drop(['企业编号'], axis=1, inplace=True)

(2364, 307) (592, 307) (2364,) (592,)


In [18]:
nfolds = 10
folds = KFold(n_splits=nfolds, shuffle=True, random_state=15)

In [19]:
def train_lgbm(xtrain, ytrain, xtest, ytest, params):
    feature_importance_df = np.zeros((xtrain.shape[1], nfolds))
    mvalid = np.zeros(len(xtrain))
    mfull = np.zeros(len(xtest))
    models = []

    for fold_, (trn_idx, val_idx) in enumerate(folds.split(xtrain.values, ytrain.values)):
        print('----')
        print("fold n°{}".format(fold_))

        x0, y0 = xtrain.iloc[trn_idx], ytrain.iloc[trn_idx]
        x1, y1 = xtrain.iloc[val_idx], ytrain.iloc[val_idx]

        trn_data = lgb.Dataset(x0, label=y0)
        val_data = lgb.Dataset(x1, label=y1)

        num_round = 10000
        clf = lgb.train(params,
                        trn_data,
                        num_round,
                        valid_sets=[trn_data, val_data],
                        verbose_eval=500,
                        early_stopping_rounds=150)

        mvalid[val_idx] = clf.predict(x1, num_iteration=clf.best_iteration)

        feature_importance_df[:, fold_] = clf.feature_importance()

        mfull += clf.predict(xtest,
                             num_iteration=clf.best_iteration) / folds.n_splits

        models.append(clf)

    test_error = np.sqrt(mean_squared_error(
        mfull.astype(int), ytest.astype(int)))
    print()
    print('rmse:', test_error)
    return models, test_error, feature_importance_df

In [20]:
params_all = {
    # objective and metric
    "objective": "regression",
    "metric": 'rmse',
    "boosting": "gbdt",

    # for the Leaf-wise (Best-first) Tree
    "num_leaves": 100,
    # smaller than 2^(max_depth), This is the main parameter to control the complexity of the tree model. With larger can get higher accuracy
    # Setting it to a large value can avoid growing too deep a tree, but may cause under-fitting.
    "min_data_in_leaf": 30,
    "max_depth": 7,  # limit the tree depth explicitly.

    # For Faster Speed
    "bagging_fraction": 0.7,
    "bagging_freq": 1,
    #     "max_bin": 5, # more small more faster
    "bagging_seed": 11,

    # For Better Accuracy
    "max_bin": 20,  # lager but slower
    "learning_rate": 0.005,

    # deal with over fitting
    # Use small max_bin
    # Use small num_leaves
    # Use min_data_in_leaf and min_sum_hessian_in_leaf
    # Use bagging by set bagging_fraction and bagging_freq
    # Use feature sub-sampling by set feature_fraction
    # Use bigger training data
    # Try lambda_l1, lambda_l2 and min_gain_to_split for regularization
    # Try max_depth to avoid growing deep tree
    "feature_fraction": 0.8,
    "lambda_l1": 0.9,

    "min_child_samples": 100,

    # other
    "n_estimators": 1500,
    "verbosity": -1,
    "n_jobs": -1,
}

In [21]:
params_range_dict = {  # for the Leaf-wise (Best-first) Tree
    "num_leaves": np.arange(10, 160, 10, dtype=int),
    # smaller than 2^(max_depth), This is the main parameter to control the complexity of the tree model. With larger can get higher accuracy
    #     "min_data_in_leaf": np.arange(10,55,5), # Setting it to a large value can avoid growing too deep a tree, but may cause under-fitting.
    # limit the tree depth explicitly.
    "max_depth": np.arange(4, 13, 1, dtype=int),

    #     # For Faster Speed
    #     "bagging_fraction": np.arange(0.5, 1,0.1),

    #     # For Better Accuracy
    "max_bin": np.arange(10, 60, 5, dtype=int),  # lager but slower

    #     "feature_fraction": np.arange(0.3, 1, 0.1),
    #     "lambda_l1": np.arange(0.01, 1, 0.05),

    #     "min_child_samples": np.arange(70, 110,10),
}

# params_range_dict ={"num_leaves": np.arange(10,30,10, dtype=int)}

In [22]:
def search_params(params_range_dict, xtrain, ytrain, xtest, ytest):
    best_rmse = np.inf
    count = 0
    train_dict = {}
    params_name = list(params_range_dict.keys())
    params_values = []
    for name in params_name:
        params_values.append(params_range_dict[name])

    c_params = list(itertools.product(*params_values))
    idx = [i for i in range(0, len(c_params))]

    params_df = pd.DataFrame(c_params, index=idx, columns=params_name)
    print('Iteration number:', len(params_df))
    for row in range(0, len(params_df)):
        print('*********************************Iteration: %s****************************************************' % str(count))
        starttime = time.time()
        each_params = params_df.iloc[row].to_dict()
        print('Current params:', each_params)
        params_all.update(each_params)
        models, test_error, feature_importance_df = train_lgbm(
            xtrain, ytrain, xtest, ytest, params_all)

        print("Used %s seconds" % (time.time() - starttime))

        count += 1

        if test_error < best_rmse:
            best_rmse = test_error
            train_dict = {'models': models, 'rmse': test_error,
                          'feature_importance': feature_importance_df, 'params': each_params}
        print('Current best:', best_rmse, 'Params:', train_dict['params'])
        print()

    return train_dict

In [ ]:
train_dict = search_params(params_range_dict, xtrain, ytrain, xtest, ytest)
train_dict

Iteration number: 1350
*********************************Iteration: 0****************************************************
Current params: {'num_leaves': 10, 'max_depth': 4, 'max_bin': 10}
----
fold n°0
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.95334	valid_1's rmse: 3.62696
[1000]	training's rmse: 2.62557	valid_1's rmse: 3.53733
[1500]	training's rmse: 2.41282	valid_1's rmse: 3.51127
Did not meet early stopping. Best iteration is:
[1500]	training's rmse: 2.41282	valid_1's rmse: 3.51127
----
fold n°1
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 3.01238	valid_1's rmse: 2.98539
[1000]	training's rmse: 2.67513	valid_1's rmse: 2.88633
Early stopping, best iteration is:
[1293]	training's rmse: 2.53672	valid_1's rmse: 2.87914
----
fold n°2
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.98382	valid_1's rmse: 3.33365
[1000]	training's rmse: 2.64734	valid_1's rmse: 3.2679

[1000]	training's rmse: 2.62396	valid_1's rmse: 3.04137
Early stopping, best iteration is:
[1188]	training's rmse: 2.53514	valid_1's rmse: 3.03545
----
fold n°6
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.96068	valid_1's rmse: 3.32344
[1000]	training's rmse: 2.62003	valid_1's rmse: 3.17666
[1500]	training's rmse: 2.39609	valid_1's rmse: 3.15827
Did not meet early stopping. Best iteration is:
[1500]	training's rmse: 2.39609	valid_1's rmse: 3.15827
----
fold n°7
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.94637	valid_1's rmse: 3.42669
[1000]	training's rmse: 2.60136	valid_1's rmse: 3.29838
Early stopping, best iteration is:
[1239]	training's rmse: 2.48692	valid_1's rmse: 3.28793
----
fold n°8
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.95951	valid_1's rmse: 3.13541
[1000]	training's rmse: 2.61093	valid_1's rmse: 3.05667
Early stopping, best iteration is:
[10

[1500]	training's rmse: 2.37282	valid_1's rmse: 3.50929
Did not meet early stopping. Best iteration is:
[1500]	training's rmse: 2.37282	valid_1's rmse: 3.50929
----
fold n°1
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.97211	valid_1's rmse: 3.00649
[1000]	training's rmse: 2.61985	valid_1's rmse: 2.9129
Early stopping, best iteration is:
[1166]	training's rmse: 2.5386	valid_1's rmse: 2.90481
----
fold n°2
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.94202	valid_1's rmse: 3.32686
[1000]	training's rmse: 2.59558	valid_1's rmse: 3.2731
Early stopping, best iteration is:
[1236]	training's rmse: 2.48523	valid_1's rmse: 3.26438
----
fold n°3
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.95261	valid_1's rmse: 3.19935
[1000]	training's rmse: 2.60766	valid_1's rmse: 3.11112
Early stopping, best iteration is:
[993]	training's rmse: 2.61095	valid_1's rmse: 3.11035
----
fo

----
fold n°7
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.92666	valid_1's rmse: 3.44263
[1000]	training's rmse: 2.57756	valid_1's rmse: 3.32374
Early stopping, best iteration is:
[1291]	training's rmse: 2.44295	valid_1's rmse: 3.31329
----
fold n°8
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.94809	valid_1's rmse: 3.13319
[1000]	training's rmse: 2.59642	valid_1's rmse: 3.06394
Early stopping, best iteration is:
[857]	training's rmse: 2.6746	valid_1's rmse: 3.06176
----
fold n°9
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.94264	valid_1's rmse: 3.27853
[1000]	training's rmse: 2.59136	valid_1's rmse: 3.19257
Early stopping, best iteration is:
[1145]	training's rmse: 2.52176	valid_1's rmse: 3.18609

rmse: 3.1249324317019567
Used 44.66820287704468 seconds
Current best: 3.1054115799811592 Params: {'num_leaves': 10, 'max_depth': 4, 'max_bin': 40}

****************

----
fold n°2
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.95716	valid_1's rmse: 3.31445
[1000]	training's rmse: 2.61122	valid_1's rmse: 3.25236
Early stopping, best iteration is:
[1255]	training's rmse: 2.49214	valid_1's rmse: 3.23947
----
fold n°3
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.9652	valid_1's rmse: 3.1636
[1000]	training's rmse: 2.62042	valid_1's rmse: 3.08368
Early stopping, best iteration is:
[1064]	training's rmse: 2.58847	valid_1's rmse: 3.08034
----
fold n°4
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.9971	valid_1's rmse: 2.93675
[1000]	training's rmse: 2.64492	valid_1's rmse: 2.79771
Early stopping, best iteration is:
[1279]	training's rmse: 2.51155	valid_1's rmse: 2.7912
----
fold n°5
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.96907	valid_1's rmse: 3.12056
[1000]	training's rmse: 2.62314	val

...

[500]	training's rmse: 2.33179	valid_1's rmse: 3.0935
[1000]	training's rmse: 1.73057	valid_1's rmse: 3.05756
Early stopping, best iteration is:
[853]	training's rmse: 1.87353	valid_1's rmse: 3.05139
----
fold n°9
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.32903	valid_1's rmse: 3.21112
[1000]	training's rmse: 1.72771	valid_1's rmse: 3.16103
Early stopping, best iteration is:
[968]	training's rmse: 1.75601	valid_1's rmse: 3.15968

rmse: 3.129253861502727
Used 75.38653111457825 seconds
Current best: 3.0975142605958403 Params: {'num_leaves': 20, 'max_depth': 12, 'max_bin': 55}

*********************************Iteration: 1319****************************************************
Current params: {'num_leaves': 150, 'max_depth': 9, 'max_bin': 55}
----
fold n°0
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.28458	valid_1's rmse: 3.54596
[1000]	training's rmse: 1.68615	valid_1's rmse: 3.49467
[1500]	training's

Early stopping, best iteration is:
[1022]	training's rmse: 1.72131	valid_1's rmse: 2.74193
----
fold n°5
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.36322	valid_1's rmse: 3.10635
[1000]	training's rmse: 1.73254	valid_1's rmse: 3.06113
Early stopping, best iteration is:
[885]	training's rmse: 1.84856	valid_1's rmse: 3.05901
----
fold n°6
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.36585	valid_1's rmse: 3.21148
[1000]	training's rmse: 1.73807	valid_1's rmse: 3.10136
Early stopping, best iteration is:
[1020]	training's rmse: 1.71999	valid_1's rmse: 3.10068
----
fold n°7
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.35757	valid_1's rmse: 3.33909
[1000]	training's rmse: 1.73169	valid_1's rmse: 3.26883
Early stopping, best iteration is:
[1128]	training's rmse: 1.61293	valid_1's rmse: 3.26747
----
fold n°8
Training until validation scores don't improve for 150 roun

Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.33631	valid_1's rmse: 2.94594
[1000]	training's rmse: 1.70751	valid_1's rmse: 2.89541
Early stopping, best iteration is:
[929]	training's rmse: 1.7755	valid_1's rmse: 2.89459
----
fold n°2
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.33242	valid_1's rmse: 3.22541
[1000]	training's rmse: 1.71651	valid_1's rmse: 3.1775
Early stopping, best iteration is:
[913]	training's rmse: 1.7977	valid_1's rmse: 3.17594
----
fold n°3
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.33823	valid_1's rmse: 3.11251
Early stopping, best iteration is:
[777]	training's rmse: 1.94862	valid_1's rmse: 3.07788
----
fold n°4
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.34255	valid_1's rmse: 2.84549
[1000]	training's rmse: 1.71213	valid_1's rmse: 2.76928
Early stopping, best iteration is:
[922]	training's


rmse: 3.1314123400221896
Used 68.31900215148926 seconds
Current best: 3.0975142605958403 Params: {'num_leaves': 20, 'max_depth': 12, 'max_bin': 55}

*********************************Iteration: 1327****************************************************
Current params: {'num_leaves': 150, 'max_depth': 10, 'max_bin': 45}
----
fold n°0
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.26984	valid_1's rmse: 3.52376
[1000]	training's rmse: 1.64502	valid_1's rmse: 3.47342
[1500]	training's rmse: 1.24966	valid_1's rmse: 3.46659
Did not meet early stopping. Best iteration is:
[1500]	training's rmse: 1.24966	valid_1's rmse: 3.46659
----
fold n°1
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.32519	valid_1's rmse: 2.93947
[1000]	training's rmse: 1.68736	valid_1's rmse: 2.8947
Early stopping, best iteration is:
[924]	training's rmse: 1.76276	valid_1's rmse: 2.89216
----
fold n°2
Training until validation scores don't imp

----
fold n°7
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.29639	valid_1's rmse: 3.34753
Early stopping, best iteration is:
[743]	training's rmse: 1.94221	valid_1's rmse: 3.29347
----
fold n°8
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.30348	valid_1's rmse: 3.08533
Early stopping, best iteration is:
[810]	training's rmse: 1.86462	valid_1's rmse: 3.03597
----
fold n°9
Training until validation scores don't improve for 150 rounds.
[500]	training's rmse: 2.30806	valid_1's rmse: 3.19616
[1000]	training's rmse: 1.67598	valid_1's rmse: 3.13548
Early stopping, best iteration is:
[879]	training's rmse: 1.79174	valid_1's rmse: 3.13406

rmse: 3.126013349213253
Used 84.03973317146301 seconds
Current best: 3.0975142605958403 Params: {'num_leaves': 20, 'max_depth': 12, 'max_bin': 55}

*********************************Iteration: 1330****************************************************
Current params: {'num_leaves